In [9]:
import pandas as pd
from datetime import datetime
import folium # visualizing weather stations
from folium.plugins import MarkerCluster
import geopandas as gpd
from shapely.geometry import Point


In [28]:

# Nicht ausführen! Sonst enstehen Kosten!
""" import requests
import pandas as pd
import numpy as np

# Ihre API-Schlüssel
API_KEY = 'API-Key'  # Ersetzen Sie durch Ihren tatsächlichen API-Schlüssel

# Basis-URL für die Places API
PLACES_URL = "https://maps.googleapis.com/maps/api/place/nearbysearch/json"

# Deutschland als Rechteck definieren (ungefährer Rahmen)
north = 55.1  # Nördlichster Punkt Deutschlands
south = 47.3  # Südlichster Punkt Deutschlands
west = 5.9    # Westlichster Punkt Deutschlands
east = 15.0   # Östlichster Punkt Deutschlands

# Raster für Deutschland erzeugen
step = 0.5  # Schrittgröße in Grad (kleiner machen für genauere Abdeckung)
latitude_points = np.arange(south, north, step)
longitude_points = np.arange(west, east, step)

# Alle Standorte in Deutschland
locations = [(lat, lon) for lat in latitude_points for lon in longitude_points]

# Suchradius (in Metern) - etwa 50 km ist oft eine gute Abdeckung
radius = 50000

# Ergebnisse sammeln
place_list = []

for location in locations:
    lat, lon = location
    params = {
        "location": f"{lat},{lon}",
        "radius": radius,
        "type": "campground",
        "key": API_KEY
    }
    
    response = requests.get(PLACES_URL, params=params)
    data = response.json()

    
    
    if data.get("status") == "OK":
        places = data.get("results")
        for place in places:
            place_info = {
                "name": place.get("name"),
                "latitude": place["geometry"]["location"]["lat"],
                "longitude": place["geometry"]["location"]["lng"],
            }
            place_list.append(place_info)
    else:
        print(f"Fehler bei der API-Anfrage für Standort {location}: {data.get('status')}")

# In ein DataFrame konvertieren
df = pd.DataFrame(place_list)

# Duplikate entfernen (basierend auf Name und Koordinaten)
df = df.drop_duplicates(subset=['name', 'latitude', 'longitude'])

# Ausgabe der Ergebnisse
print(df.head(10))
 """

Fehler bei der API-Anfrage für Standort (54.3, 5.9): ZERO_RESULTS
Fehler bei der API-Anfrage für Standort (54.3, 6.4): ZERO_RESULTS
Fehler bei der API-Anfrage für Standort (54.3, 6.9): ZERO_RESULTS
Fehler bei der API-Anfrage für Standort (54.8, 5.9): ZERO_RESULTS
Fehler bei der API-Anfrage für Standort (54.8, 6.4): ZERO_RESULTS
Fehler bei der API-Anfrage für Standort (54.8, 6.9): ZERO_RESULTS
Fehler bei der API-Anfrage für Standort (54.8, 7.4): ZERO_RESULTS
                                       name   latitude  longitude
0                         Camping Le Chanet  47.100115   6.127881
1             Camping Municipal La Louvière  47.581648   5.875957
2                 Camping*** les Promenades  47.104214   5.887304
3                      Camping l' Esplanade  47.358454   6.078866
4                        Camping Verte Rive  47.357635   6.081029
5                          Camping de l'île  47.147618   5.725626
6                 Woka Camping Green Lagoon  47.289744   5.777419
7         

In [29]:
map_deutschland = folium.Map(location=[51.1657, 10.4515], zoom_start=6)

# Marker Cluster erstellen
marker_cluster = MarkerCluster().add_to(map_deutschland)

# Wetterstationen hinzufügen
for index, row in df.iterrows():
    folium.Marker(location=[row['latitude'], row['longitude']],
                  popup=row['name']).add_to(marker_cluster)
 
map_deutschland

In [32]:
""" current_datetime = datetime.now().strftime('%Y%m%d_%H%M%S')
df.to_csv(f"../Data_Lake/campingplaetze_{current_datetime}.csv", index=False)
df.to_csv(f"../Temp_DWH/campingplaetze.csv", index=False) """	

: 

In [3]:
df = pd.read_csv("../Temp_DWH/campingplaetze.csv")
df

name   latitude  longitude
0                        Camping Le Chanet  47.100115   6.127881
1            Camping Municipal La Louvière  47.581648   5.875957
2                Camping*** les Promenades  47.104214   5.887304
3                     Camping l' Esplanade  47.358454   6.078866
4                       Camping Verte Rive  47.357635   6.081029
...                                    ...        ...        ...
2403                 Shelterplads Snogebæk  55.026542  15.120895
2404                    Eco Beach Camp Aps  55.036036  15.108443
2405  Wohnmobilparkplatz am Hafen von Nexø  55.058647  15.137795
2406                     Pedersker Jagthus  55.089864  15.002383
2407            Nexø Camping & Feriehytter  55.072654  15.141465

[2408 rows x 3 columns]

In [10]:
def create_geometry(row):
    return Point(row['longitude'], row['latitude'])

# Geometry-Spalte hinzufügen
df['geometry'] = df.apply(create_geometry, axis=1)

# Normales DataFrame in ein GeoDataFrame umwandeln
gdf = gpd.GeoDataFrame(df, geometry='geometry')

# Optional: Setzen des CRS (Koordinatensystems) - hier verwenden wir WGS 84
gdf.set_crs(epsg=4326, inplace=True)


name   latitude  longitude  \
0                        Camping Le Chanet  47.100115   6.127881   
1            Camping Municipal La Louvière  47.581648   5.875957   
2                Camping*** les Promenades  47.104214   5.887304   
3                     Camping l' Esplanade  47.358454   6.078866   
4                       Camping Verte Rive  47.357635   6.081029   
...                                    ...        ...        ...   
2403                 Shelterplads Snogebæk  55.026542  15.120895   
2404                    Eco Beach Camp Aps  55.036036  15.108443   
2405  Wohnmobilparkplatz am Hafen von Nexø  55.058647  15.137795   
2406                     Pedersker Jagthus  55.089864  15.002383   
2407            Nexø Camping & Feriehytter  55.072654  15.141465   

                       geometry  
0      POINT (6.12788 47.10011)  
1      POINT (5.87596 47.58165)  
2      POINT (5.88730 47.10421)  
3      POINT (6.07887 47.35845)  
4      POINT (6.08103 47.35763)  
...                         ...  
2403  POINT (15.12090 55.02654)  
2404  POINT (15.10844 55.03604)  
2405  POINT (15.13780 55.05865)  
2406  POINT (15.00238 55.08986)  
2407  POINT (15.14147 55.07265)  

[2408 rows x 4 columns]

In [15]:
map_deutschland = folium.Map(location=[51.1657, 10.4515], zoom_start=6)

# Marker Cluster erstellen
marker_cluster = MarkerCluster().add_to(map_deutschland)

for index, row in gdf.iterrows():
    point = row.geometry  # Annahme: Die geometrische Spalte heißt 'geometry'
    latitude = point.y
    longitude = point.x
    folium.Marker(location=[latitude, longitude], popup=row['name']).add_to(marker_cluster)
 
map_deutschland

In [16]:
deutschland = gpd.read_file("../Data_Lake/deutschland.geo.json")
df_deutschland = gdf.copy()
for i in range(0,len(df_deutschland)):
    if not deutschland.contains(df_deutschland.geometry[i]).any():
        df_deutschland = df_deutschland.drop(i, axis=0)

In [19]:

map_deutschland2 = folium.Map(location=[51.1657, 10.4515], zoom_start=6)

# Marker Cluster erstellen
marker_cluster = MarkerCluster().add_to(map_deutschland2)

# Wetterstationen hinzufügen
for index, row in df_deutschland.iterrows():
    folium.Marker(location=[row['latitude'], row['longitude']],
                  popup=row['name']).add_to(marker_cluster)
    
map_deutschland2

In [20]:
kreise = gpd.read_file("../Data_Lake/kreise.geo.json")
df_kreise = df_deutschland.copy()
def find_kreis(point, gdf_kreise):
    for index, row in gdf_kreise.iterrows():
        if row['geometry'].contains(point):
            return row['NAME_3']  # Hier den Namen der tatsächlichen Spalte für die Bundesländer anpassen

# Konvertierung von Breiten- und Längengraden in Point-Objekte
df_kreise['kreis'] = df_kreise['geometry'].apply(lambda point: find_kreis(point, kreise))

In [21]:
df_kreise

name   latitude  longitude  \
64                                Camping Hochrhein  47.604788   8.299681   
90                         Camping Gitzenweiler Hof  47.584940   9.706269   
91                           Campingplatz Fischbach  47.669320   9.403940   
92    CAP-Rotach gGmbH Hotel - Restaurant - Camping  47.649900   9.496433   
94                          Ravensburger Spieleland  47.709730   9.592004   
...                                             ...        ...        ...   
2373                        Surf and Kite Camp Wiek  54.628414  13.288874   
2374                         Campingplatz Drewoldke  54.634331  13.373580   
2375      Caravan Camp "Baltic Sea" Dranske / Rügen  54.628993  13.222769   
2377  OSTSEEWIND - Camping + Appartements auf Rügen  54.659890  13.259641   
2379                                Landgut Dargast  54.531665  13.610358   

                       geometry     kreis  
64     POINT (8.29968 47.60479)  Waldshut  
90     POINT (9.70627 47.58494)    Lindau  
91     POINT (9.40394 47.66932)  Bodensee  
92     POINT (9.49643 47.64990)      None  
94     POINT (9.59200 47.70973)  Bodensee  
...                         ...       ...  
2373  POINT (13.28887 54.62841)     Rügen  
2374  POINT (13.37358 54.63433)     Rügen  
2375  POINT (13.22277 54.62899)     Rügen  
2377  POINT (13.25964 54.65989)     Rügen  
2379  POINT (13.61036 54.53167)     Rügen  

[1420 rows x 5 columns]

In [22]:
cleaned_data = pd.merge(df_kreise, kreise, left_on="kreis", right_on="NAME_3")
columns = ["ID_0", "ISO", "NAME_0", "ID_1", "ID_2", "ID_3", "kreis", "NL_NAME_3", "ENGTYPE_3", "geometry_y", "VARNAME_3"]
cleaned_data = cleaned_data.drop(columns, axis=1)
cleaned_data = cleaned_data.rename(columns={"geometry_x": "geometry", "NAME_1": "Bundesland", "NAME_2" : "Regierungsbezirk", "NAME_3": "Kreis", "TYPE_3":"Typ"})
cleaned_data

name   latitude  longitude  \
0                                 Camping Hochrhein  47.604788   8.299681   
1                          Camping Gitzenweiler Hof  47.584940   9.706269   
2                            Campingplatz Fischbach  47.669320   9.403940   
3                           Ravensburger Spieleland  47.709730   9.592004   
4                                         Rubi-Camp  47.423770  10.278400   
...                                             ...        ...        ...   
1405                        Surf and Kite Camp Wiek  54.628414  13.288874   
1406                         Campingplatz Drewoldke  54.634331  13.373580   
1407      Caravan Camp "Baltic Sea" Dranske / Rügen  54.628993  13.222769   
1408  OSTSEEWIND - Camping + Appartements auf Rügen  54.659890  13.259641   
1409                                Landgut Dargast  54.531665  13.610358   

                       geometry              Bundesland  \
0      POINT (8.29968 47.60479)       Baden-Württemberg   
1      POINT (9.70627 47.58494)                  Bayern   
2      POINT (9.40394 47.66932)       Baden-Württemberg   
3      POINT (9.59200 47.70973)       Baden-Württemberg   
4     POINT (10.27840 47.42377)                  Bayern   
...                         ...                     ...   
1405  POINT (13.28887 54.62841)  Mecklenburg-Vorpommern   
1406  POINT (13.37358 54.63433)  Mecklenburg-Vorpommern   
1407  POINT (13.22277 54.62899)  Mecklenburg-Vorpommern   
1408  POINT (13.25964 54.65989)  Mecklenburg-Vorpommern   
1409  POINT (13.61036 54.53167)  Mecklenburg-Vorpommern   

            Regierungsbezirk       Kreis         Typ  
0                   Freiburg    Waldshut  Landkreise  
1                   Schwaben      Lindau  Landkreise  
2                   Tübingen    Bodensee  Landkreise  
3                   Tübingen    Bodensee  Landkreise  
4                   Schwaben  Oberallgäu  Landkreise  
...                      ...         ...         ...  
1405  Mecklenburg-Vorpommern       Rügen  Landkreise  
1406  Mecklenburg-Vorpommern       Rügen  Landkreise  
1407  Mecklenburg-Vorpommern       Rügen  Landkreise  
1408  Mecklenburg-Vorpommern       Rügen  Landkreise  
1409  Mecklenburg-Vorpommern       Rügen  Landkreise  

[1410 rows x 8 columns]

In [23]:
current_datetime = datetime.now().strftime('%Y%m%d_%H%M%S')
cleaned_data.to_csv(f"../Data_Lake/campingplaetze_{current_datetime}.csv", index=False)
cleaned_data.to_csv(f"../Temp_DWH/campingplaetze.csv", index=False)